# Prepare Weather Data for Training

In [2]:
import pandas as pd
import os
from pathlib import Path
import numpy as np

## Find the total number of weather params in our data

In [3]:
def get_all_weather_params(weather_params):
    base_path = '../data/processing/final-weather'
    for year_folder in os.listdir(base_path):
        year_path = os.path.join(base_path, year_folder)

        for week_num in range(1, 53):
            week_path = os.path.join(year_path, f'week_{week_num}')

            if not os.path.exists(week_path):
                print(f"Path {week_path} does not exist")
                continue

            file_list = Path(week_path).glob('*')

            for fine_area in file_list:
                fine_area_df = pd.read_csv(fine_area, skipinitialspace=True)  # skipinitialspace to remove extra spaces in column names
                weather_params.update(fine_area_df.columns)

In [4]:
weather_params = set()
get_all_weather_params(weather_params)
print(weather_params)
print(len(weather_params))

{'WSPD_SCLR', 'wind_direction', 'avg_rel_hum_pst1hr', 'HUMIDITY', 'wind_gust_speed', 'snwfl_amt_pst1hr', 'WIND_DIRECTION_STD_DEVIATION1', 'MEASURED_WIND_SPEED1', 'pcpn_amt_pst24hrs', 'tendency_amount', 'AirTemp', 'avg_air_temp_pst1hr', 'MAXIMUM_MEASURED_WIND_SPEED1', 'dwpt_temp', 'MIN_TEMP', 'rnfl_amt_pst24hrs', 'CURRENT_AIR_TEMPERATURE1', 'ACTUAL_WIND_SPEED', 'MEASURED_WIND_DIRECTION1', 'WDIR_VECT', 'relative_humidity', 'time', 'MAX_TEMP', 'rnfl_amt_pst1hr', 'wind_speed', 'ACTUAL_WIND_DIRECTION', 'temperature', 'snw_dpth', 'CURRENT_AIR_TEMPERATURE2', 'stn_pres', 'MINIMUM_AIR_TEMPERATURE', 'cum_pcpn_amt', 'snw_dpth_wtr_equiv', 'mean_sea_level', 'MAXIMUM_AIR_TEMPERATURE', 'air_temperature_yesterday_high', 'avg_wnd_dir_10m_pst10mts', 'ONE_DAY_SNOW', 'avg_wnd_spd_10m_pst10mts', 'air_temperature_yesterday_low', 'TEMP_MEAN', 'STANDARD_SNOW', 'min_air_temp_snc_last_reset', 'SWE', 'DEW_POINT', 'HEIGHT_OF_SNOW', 'PRECIPITATION_NEW', 'air_temp_2', 'dew_point', 'max_wnd_spd_10m_pst1hr', 'ONE_DAY

## Group by week

In [5]:
def create_weather_df(long_splits, lat_splits, weather_params, all_week_dfs):
    num_fine_areas = long_splits * lat_splits

    base_path = '../data/processing/final-weather'
    for year_num in range(2017, 2023):
        year_path = os.path.join(base_path, str(year_num))
        if not os.path.exists(year_path):
            print(f"Path {year_path} does not exist")
            continue

        for week_num in range(1, 53):
            week_path = os.path.join(year_path, f'week_{week_num}')
            if not os.path.exists(week_path):
                print(f"Path {week_path} does not exist")
                continue

            # create the 36 * 67 weekly dataframe
            week_df = pd.DataFrame(columns=weather_params)
            for i in range(1, num_fine_areas + 1):
                fine_area_path = week_path + f'/fine_area_{i}_weather.csv'
                print("Reading file: ", fine_area_path)

                # average the fine areas and add the averaged row to the dataframe
                if os.path.exists(fine_area_path):
                    fine_area_df = pd.read_csv(fine_area_path, skipinitialspace=True)
                    # Convert columns to numeric, handling errors with coerce to replace invalid values with NaN
                    fine_area_df = fine_area_df.apply(pd.to_numeric, errors='coerce')
                    # Calculate average of each column
                    averaged_row = fine_area_df.mean(axis=0).to_frame().T
                    averaged_row = averaged_row.reindex(columns=weather_params, fill_value=np.nan)

                    week_df = pd.concat([week_df, averaged_row], ignore_index=True)

                # add an empty row to the dataframe
                else:
                    empty_row = pd.DataFrame(columns=weather_params)
                    new_row = [float('nan')] * len(empty_row.columns)
                    empty_row.loc[len(empty_row)] = new_row
                    week_df = pd.concat([week_df, empty_row], ignore_index=True)

            # add the week_df to the list of all week dataframes
            all_week_dfs.append(week_df)


In [ ]:
all_week_dfs = []
long_splits = 6
lat_splits = 6

create_weather_df(long_splits, lat_splits, list(weather_params), all_week_dfs)

In [7]:
len(all_week_dfs)

312

### Test null cell threshold

In [8]:
weather_params_to_remove = set()

for df in all_week_dfs:
    threshold = 0.9
    nan_threshold = len(df) * threshold
    columns_to_drop = df.columns[df.isna().sum() > nan_threshold].tolist()
    weather_params_to_remove.update(columns_to_drop)

print(len(weather_params_to_remove))

63


In [9]:
params_to_keep = weather_params.difference(weather_params_to_remove)
print(params_to_keep)
print(len(params_to_keep) - 1)

{'week_of_year', 'pcpn_amt_pst1hr', 'MIN_TEMP', 'MAX_TEMP'}
3


## Group by a year

In [44]:
dfs = all_week_dfs

# Define the number of dataframes in each group
num_dataframes_in_group = 52

# Calculate the number of groups
num_groups = len(dfs) // num_dataframes_in_group

# Create an empty list to store the new dataframes for each group
grouped_dfs = []

# Loop through each group
for group_num in range(num_groups):
    # Extract the dataframes for the current group
    current_group = dfs[group_num * num_dataframes_in_group : (group_num + 1) * num_dataframes_in_group]

    # Create a new dataframe for the current group with the same dimensions
    new_df = pd.DataFrame(index=current_group[0].index, columns=current_group[0].columns)

    # Calculate the average for each cell in the new dataframe
    for col in new_df.columns:
        for row in new_df.index:
            values = [df.loc[row, col] for df in current_group if pd.notna(df.loc[row, col])]
            if values:  # Check if values is not empty
                avg_value = np.mean(values)
                new_df.loc[row, col] = avg_value

    # Append the new dataframe to the list
    grouped_dfs.append(new_df)

In [74]:
new_weather_params_to_remove = set()

i = 2016

for df in grouped_dfs:
    # df.to_csv(f'grouped_weather_year_{i}.csv', index=False)
    # i += 1
    threshold = 0.5
    nan_threshold = len(df) * threshold
    columns_to_drop = df.columns[df.isna().sum() > nan_threshold].tolist()
    new_weather_params_to_remove.update(columns_to_drop)

In [75]:
print(len(new_weather_params_to_remove))
opposite_result = weather_params.difference(new_weather_params_to_remove)
print(opposite_result)

61
{'wind_direction', 'relative_humidity', 'week_of_year', 'precipitation', 'temperature', 'wind_speed'}


## Group by months

In [110]:
dfs = all_week_dfs

# Define the number of dataframes in each group
num_dataframes_in_group = 4

# Calculate the number of groups
num_groups = len(dfs) // num_dataframes_in_group

# Create an empty list to store the new dataframes for each group
grouped_dfs = []

# Loop through each group
for group_num in range(num_groups):
    # Extract the dataframes for the current group
    current_group = dfs[group_num * num_dataframes_in_group : (group_num + 1) * num_dataframes_in_group]

    # Create a new dataframe for the current group with the same dimensions
    new_df = pd.DataFrame(index=current_group[0].index, columns=current_group[0].columns)

    # Calculate the average for each cell in the new dataframe
    for col in new_df.columns:
        for row in new_df.index:
            values = [df.loc[row, col] for df in current_group if pd.notna(df.loc[row, col])]
            if values:  # Check if values is not empty
                avg_value = np.mean(values)
                new_df.loc[row, col] = avg_value

    # Append the new dataframe to the list
    grouped_dfs.append(new_df)

In [111]:
len(grouped_dfs)

78

### Test null cell threshold

In [112]:
new_weather_params_to_remove = set()

for df in grouped_dfs:
    threshold = 0.95
    nan_threshold = len(df) * threshold
    columns_to_drop = df.columns[df.isna().sum() > nan_threshold].tolist()
    new_weather_params_to_remove.update(columns_to_drop)

In [113]:
print(len(new_weather_params_to_remove))
opposite_result = weather_params.difference(new_weather_params_to_remove)
print(opposite_result)

50
{'wind_direction', 'MIN_TEMP', 'MAX_TEMP', 'relative_humidity', 'mean_sea_level', 'ONE_DAY_PRECIPITATION', 'wind_speed', 'dew_point', 'wind_gust_speed', 'week_of_year', 'air_temperature', 'pcpn_amt_pst1hr', 'snw_dpth', 'snw_dpth_wtr_equiv', 'tendency_amount', 'total_precipitation', 'air_temp_1'}


In [32]:
columns_to_drop = list(new_weather_params_to_remove)
columns_to_drop.append('week_of_year')
group = 1
for df in grouped_dfs:
    df.drop(columns=columns_to_drop, inplace=True)
    df.to_csv(f'../data/prepared/monthly-6-by-6/weather/group_{group}.csv', index=False)
    group += 1

### Monthly Time Interpolation

In [114]:
year_grouped_months = []
month_grouped = []

i = 0
for df in grouped_dfs:
    month_grouped.append(df)
    i += 1
    if i % 12 == 0:
        year_grouped_months.append(month_grouped)
        month_grouped = []

In [115]:
year_interp_range = 1
count = 0

for year_i in range(len(year_grouped_months)):
    month_dfs = year_grouped_months[year_i]

    for month_i in range(len(month_dfs)):
        month_df = month_dfs[month_i]

        for row in month_df.index:
            for col in month_df.columns:
                
                if pd.isna(month_df.loc[row, col]):
                    interp_vals = []

                    for interp_step in range (1, year_interp_range + 1):
                        # check previous year
                        if year_i - interp_step >= 0: 
                            if year_grouped_months[year_i - interp_step][month_i].loc[row, col]:
                                df = year_grouped_months[year_i - interp_step][month_i]
                                if not pd.isna(df.loc[row, col]):
                                    val = year_grouped_months[year_i - interp_step][month_i].loc[row, col]
                                    interp_vals.append(val)

                        # check next year
                        if year_i + interp_step < len(year_grouped_months):
                            if year_grouped_months[year_i + interp_step][month_i].loc[row, col]:
                                df = year_grouped_months[year_i + interp_step][month_i]
                                if not pd.isna(df.loc[row, col]):
                                    val = year_grouped_months[year_i + interp_step][month_i].loc[row, col]
                                    interp_vals.append(val)

                    if len(interp_vals) <= 0:
                        print("interp step not big enough")
                        count += 1
                        # break
                    else: 
                        avg_interp_val = np.mean(interp_vals)
                        month_df.loc[row, col] = avg_interp_val

interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
interp step not big enough
i

In [116]:
grouped_dfs = []

print(len(year_grouped_months))
print(len(year_grouped_months[0]))

for year_i in range(len(year_grouped_months)):
    month_dfs = year_grouped_months[year_i]

    for month_i in range(len(month_dfs)):
        month_df = month_dfs[month_i]
        grouped_dfs.append(month_df)

6
12
   max_wnd_spd_10m_pst1hr ACTUAL_WIND_SPEED rnfl_amt_pst1hr HEIGHT_OF_SNOW  \
0                     NaN               NaN             NaN            NaN   
1                     NaN               NaN             NaN            NaN   
2                     NaN               NaN             NaN            NaN   
3                     NaN               NaN             NaN            NaN   
4                     NaN               NaN             NaN            NaN   
5                     NaN               NaN             NaN            NaN   
6                     NaN               NaN             NaN      92.484168   
7                     NaN               NaN             NaN            NaN   
8                     NaN               NaN             NaN            NaN   
9                     NaN               NaN             NaN      52.874068   
10                    NaN               NaN             NaN            NaN   
11                    NaN               NaN             NaN

In [117]:
len(grouped_dfs)

72

### Test monthly time interpolated null cell threshold

In [120]:
new_weather_params_to_remove = set()

for df in grouped_dfs:
    threshold = 0.7
    nan_threshold = len(df) * threshold
    columns_to_drop = df.columns[df.isna().sum() > nan_threshold].tolist()
    new_weather_params_to_remove.update(columns_to_drop)

In [121]:
print(len(grouped_dfs[0].columns))
print(len(new_weather_params_to_remove))
opposite_result = weather_params.difference(new_weather_params_to_remove)
print(len(opposite_result))
print(opposite_result)

67
61
6
{'wind_direction', 'relative_humidity', 'week_of_year', 'precipitation', 'temperature', 'wind_speed'}


In [122]:
columns_to_drop = list(new_weather_params_to_remove)
columns_to_drop.append('week_of_year')
group = 1
for df in grouped_dfs:
    df.drop(columns=columns_to_drop, inplace=True)
    df.to_csv(f'../data/prepared/monthly-6-by-6/weather-interpolated/group_{group}.csv', index=False)
    group += 1

## Group quarterly

In [10]:
dfs = all_week_dfs

# Define the number of dataframes in each group
num_dataframes_in_group = 13

# Calculate the number of groups
num_groups = len(dfs) // num_dataframes_in_group

# Create an empty list to store the new dataframes for each group
grouped_dfs = []

# Loop through each group
for group_num in range(num_groups):
    # Extract the dataframes for the current group
    current_group = dfs[group_num * num_dataframes_in_group : (group_num + 1) * num_dataframes_in_group]

    # Create a new dataframe for the current group with the same dimensions
    new_df = pd.DataFrame(index=current_group[0].index, columns=current_group[0].columns)

    # Calculate the average for each cell in the new dataframe
    for col in new_df.columns:
        for row in new_df.index:
            values = [df.loc[row, col] for df in current_group if pd.notna(df.loc[row, col])]
            if values:  # Check if values is not empty
                avg_value = np.mean(values)
                new_df.loc[row, col] = avg_value

    # Append the new dataframe to the list
    grouped_dfs.append(new_df)

In [11]:
len(grouped_dfs)

24

### Test null cell threshold

In [12]:
new_weather_params_to_remove = set()

for df in grouped_dfs:
    threshold = 0.53
    nan_threshold = len(df) * threshold
    columns_to_drop = df.columns[df.isna().sum() > nan_threshold].tolist()
    new_weather_params_to_remove.update(columns_to_drop)

In [13]:
print(len(new_weather_params_to_remove))
opposite_result = weather_params.difference(new_weather_params_to_remove)
print(len(opposite_result) - 1)
print(opposite_result)

61
5
{'wind_direction', 'week_of_year', 'precipitation', 'relative_humidity', 'wind_speed', 'temperature'}


In [14]:
columns_to_drop = list(new_weather_params_to_remove)
columns_to_drop.append('week_of_year')
group = 1
for df in grouped_dfs:
    df.drop(columns=columns_to_drop, inplace=True)
    # df.to_csv(f'../data/prepared/quarterly-6-by-6/weather/group_{group}.csv', index=False)
    group += 1

## Spatial Data Interpolation

In [19]:
# Convert flattened index to row, column coordinates
def index_to_coordinates(index, num_cols):
    row = index // num_cols
    col = index % num_cols
    return row, col

# Convert row, column coordinates to flattened index
def coordinates_to_index(row, col, num_cols):
    return row * num_cols + col

def calculate_average(df, interpolated_df, index, weather_param_index, num_cols, depth):
    i, j = index_to_coordinates(index, num_cols)

    # Check if max depth is exceeded
    if (
        max(0, i - depth) == 0
        and max(0, j - depth) == 0
        and min(len(df) // num_cols, i + depth + 1) == len(df) // num_cols
        and min(num_cols, j + depth + 1) == num_cols
    ):
        print(f"max depth exceeded for index {index}")
        return

    neighbors_sum = 0
    count = 0

    # Iterate over the neighboring cells
    for x in range(max(0, i - depth), min(len(df) // num_cols, i + depth + 1)):
        for y in range(max(0, j - depth), min(num_cols, j + depth + 1)):
            if x == i and y == j:
                continue
            neighbor_index = coordinates_to_index(x, y, num_cols)

            if pd.notna(df.iloc[neighbor_index][weather_param_index]):
                neighbors_sum += df.iloc[neighbor_index][weather_param_index]
                count += 1

    # Calculate the average
    if count > 0:
        interpolated_df.iloc[index, weather_param_index] = neighbors_sum / count
    else:
        calculate_average(df, interpolated_df, index, weather_param_index, num_cols, depth + 1)  # If there are no neighbors, keep the current value

    return

def interpolate_df(df, num_cols):
    interpolated_df = df.copy()

    # Iterate over each weather parameter
    for i in range(len(df)):
        for j in range(len(df.columns)):

            # if weather parameter is missing, interpolate by taking the average of its neighbors
            if pd.isna(df.iloc[i, j]):
                calculate_average(df, interpolated_df, i, j, num_cols, 1)

    return interpolated_df


num_cols = 6 # number of longitude splits on our map
group = 1

for df in grouped_dfs:
    interpolated_df = interpolate_df(df, num_cols)
    interpolated_df.to_csv(f'../data/prepared/quarterly-6-by-6/weather/group_{group}.csv', index=False)
    group += 1